In [1]:
import numpy

In [52]:
smallest = numpy.finfo(1.0).tiny

diff_step = 1e-1

def similar_fit_norm(a, b):
    "we only need a parameter to 4 digits of accuracy so have the pareto front only keep up to 5 digits for members of the front"
    a = numpy.absolute(numpy.array(a))
    b = numpy.absolute(numpy.array(b))

    # used to catch division by zero
    a[a == 0.0] = smallest

    a = numpy.log(a)
    b = numpy.log(b)
    
    #print("a", a)
    #print("b", b)

    diff = numpy.abs((a - b) / a)
    #print("diff", diff)
    return numpy.all(diff < diff_step)

In [62]:
def similar_fit_norm_test(a,b):
    return numpy.allclose(a,b, rtol=1e-3)

In [71]:
a = numpy.random.random([10,15])
b = a * (1+1e-3)

In [72]:
test = []
test_np = []
max_diff = []
for row_a, row_b in zip(a,b):
    test.append(similar_fit_norm(row_a, row_b))
    test_np.append(similar_fit_norm_test(row_a, row_b))
    max_diff.append(numpy.max(numpy.abs(row_a - row_b)))
    
print(test)
print(test_np)

for idx, (row_a, row_b) in enumerate(zip(a,b)):
    if test[idx] != test_np[idx]:
        print(idx, row_a, "\n", row_b)

[True, True, True, True, True, True, True, True, True, False]
[True, True, True, True, True, True, True, True, True, True]
9 [0.76458477 0.99299589 0.13151757 0.97088112 0.3373054  0.67172113
 0.99503895 0.73344691 0.38275422 0.93060393 0.6676833  0.82543424
 0.64613622 0.15392951 0.22813386] 
 [0.76534936 0.99398889 0.13164909 0.971852   0.3376427  0.67239286
 0.99603399 0.73418036 0.38313698 0.93153453 0.66835098 0.82625968
 0.64678235 0.15408344 0.228362  ]


In [22]:
print(a[0], b)

[0.46823387 0.2562123  0.45710123 0.57811548 0.31010422 0.06539451
 0.61790065 0.87375823 0.94963033 0.18136892 0.97783908 0.43992646
 0.90205403 0.40410459 0.88213348] [4.68233867e-08 2.56212302e-08 4.57101229e-08 5.78115481e-08
 3.10104224e-08 6.53945055e-09 6.17900653e-08 8.73758233e-08
 9.49630334e-08 1.81368919e-08 9.77839080e-08 4.39926461e-08
 9.02054029e-08 4.04104591e-08 8.82133476e-08]


In [49]:
similar_fit_norm(a[1], b[1])

a [-2.76003632e+00 -3.84479768e-01 -3.66763259e-01 -1.10402683e-04
 -2.77337291e+00 -2.78846272e-01 -1.30503108e-01 -7.28890103e-01
 -5.42851922e-01 -1.64114487e+00 -1.01530195e+00 -1.43024927e+00
 -2.28709576e-02 -3.25473151e+00 -9.98020648e-01]
b [-2.75903682e+00 -3.83480267e-01 -3.65763759e-01  8.89097650e-04
 -2.77237341e+00 -2.77846772e-01 -1.29503608e-01 -7.27890603e-01
 -5.41852421e-01 -1.64014537e+00 -1.01430245e+00 -1.42924977e+00
 -2.18714572e-02 -3.25373200e+00 -9.97021148e-01]
diff [3.62133036e-04 2.59961750e-03 2.72519209e-03 9.05322503e+00
 3.60391612e-04 3.58441347e-03 7.65882397e-03 1.37126342e-03
 1.84120253e-03 6.09026268e-04 9.84436539e-04 6.98829466e-04
 4.37017265e-02 3.07091486e-04 1.00148262e-03]


False

In [51]:
numpy.log(0.9998896), numpy.log(1.00088949)

(-0.0001104060945285164, 0.0008890946381995403)

In [88]:
import array
from dataclasses import dataclass
import attr

In [317]:
from typing import Iterable

def seq2array(x: Iterable[float]) -> array.array:
    return array.array("d", x)

class SetterProperty():
    def __init__(self, func):
        self.func = func
        self.__doc__ = func.__doc__
    def __set__(self, obj, value):
        return self.func(obj, value)

@attr.s
class Fitness:
    "designed for DEAP compatibility but only minimization, clean and array.array"
    _values = attr.ib(converter=seq2array)
    
    @property
    def values(self):
        return self._values
    
    @values.setter
    def values(self, value):
        self._values = seq2array(value)

    @values.deleter
    def values(self):
        del self._values
    
    @property
    def valid(self):
        return len(self.values) != 0
    
    def dominates(self, other, obj=slice(None)):
        """Return true if each objective of *self* is not strictly worse than
        the corresponding objective of *other* and at least one objective is
        strictly better.
        :param obj: Slice indicating on which objectives the domination is
                    tested. The default value is `slice(None)`, representing
                    every objectives.
        """
        dominate = False
        for self_value, other_value in zip(self.values[obj], other.values[obj]):
            if self_value < other_value:
                dominate = True
            elif self_value > other_value:
                return False
        return dominate
    
@attr.s
class Individual:
    value = attr.ib(converter=seq2array)
    fitness = attr.ib(converter=Fitness, default=attr.Factory(list))
    best = attr.ib(default=False)
    
    def __array__(self):
        return numpy.frombuffer(self.value)
    
    @property
    def valid(self):
        return self.feature.valid

In [289]:
featureA = Feature(a[0])
featureB = Feature(b[0])

In [290]:
type(feature.values)

print(featureA)

Feature(_values=array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703]))


In [184]:
Feature(1.0)

TypeError: 'float' object is not iterable

In [86]:
array.array("d", a[0])

array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703])

In [95]:
feature.values

array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703])

In [96]:
array.array("d", ['test', 'best'])

TypeError: must be real number, not str

In [107]:
similar_fit_norm_test(featureA.values, featureB.values)

True

In [109]:
featureA > featureB

False

In [309]:
indA = Individual(a[0])

In [298]:
print(indA)
print(indA.valid)

Individual(value=array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703]), fitness=Fitness(_values=array('d')), best=False)


AttributeError: 'Individual' object has no attribute 'feature'

In [191]:
indA.feature.values = a[1]

In [192]:
print(indA)
print(indA.valid)

Individual(value=array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703]), feature=Feature(_values=array('d', [0.2751399141548847, 0.48397836717273524, 0.26845359781616895, 0.6363948281466425, 0.7274881371820765, 0.9377380397369429, 0.15267184350140717, 0.11763036914351765, 0.8590285582650676, 0.24691553846813707, 0.07561431345082548, 0.21892941188534176, 0.09635701302377753, 0.08593256349214051, 0.6802871370773926])))
True


In [193]:
indB = Individual(a[0], a[1])

In [194]:
indA < indB

False

In [195]:
indA

Individual(value=array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703]), feature=Feature(_values=array('d', [0.2751399141548847, 0.48397836717273524, 0.26845359781616895, 0.6363948281466425, 0.7274881371820765, 0.9377380397369429, 0.15267184350140717, 0.11763036914351765, 0.8590285582650676, 0.24691553846813707, 0.07561431345082548, 0.21892941188534176, 0.09635701302377753, 0.08593256349214051, 0.6802871370773926])))

In [196]:
indB

Individual(value=array('d', [0.6136231632765707, 0.9662635027089004, 0.19173195435817525, 0.04498220280803644, 0.06106916517015393, 0.7076746003603497, 0.08571072881056563, 0.03806012832905059, 0.9237273140579347, 0.6938701271262935, 0.9257814322755095, 0.7534715609871386, 0.8068652109715084, 0.8497815035512017, 0.8708572793418703]), feature=Feature(_values=array('d', [0.2751399141548847, 0.48397836717273524, 0.26845359781616895, 0.6363948281466425, 0.7274881371820765, 0.9377380397369429, 0.15267184350140717, 0.11763036914351765, 0.8590285582650676, 0.24691553846813707, 0.07561431345082548, 0.21892941188534176, 0.09635701302377753, 0.08593256349214051, 0.6802871370773926])))

In [197]:
indA.feature.dominates(indB.feature)

False

In [198]:
indB.feature.dominates(indA.feature)

False

In [452]:
from addict import Dict


import copy
import math
import multiprocessing
from operator import eq

import numpy
from deap import tools

import bisect
import hashlib

class ParetoFront:
    "Modification of the pareto front in DEAP that takes cache as an argument to update to use for similar comparison"

    def __init__(self, similar=None, similar_fit=None, slice_object=slice(None)):
        if similar is None:
            similar = eq
        
        if similar_fit is not None:
            self.similar_fit = similar_fit
        else:
            self.similar_fit = eq
        
        self.slice_object = slice_object
        self.keys = list()
        self.items = list()
        self.similar = similar

    def insert(self, item):
        """Insert a new item in sorted order"""
        item = copy.deepcopy(item)
        i = bisect.bisect(self.keys, item.fitness)
        self.items.insert(i, item)
        self.keys.insert(i, item.fitness)

    def remove(self, index):
        del self.keys[index]
        del self.items[index]

    def clear(self):
        del self.items[:]
        del self.keys[:]

    def __len__(self):
        return len(self.items)

    def __getitem__(self, i):
        return self.items[i]

    def __iter__(self):
        return iter(self.items)

    def __reversed__(self):
        return reversed(self.items)
    
    def __str__(self):
        return str(self.items)

    def update(self, population, numGoals):
        """Update the Pareto front hall of fame with the *population* by adding
        the individuals from the population that are not dominated by the hall
        of fame. If any individual in the hall of fame is dominated it is
        removed.

        :param population: A list of individual with a fitness attribute to
                           update the hall of fame with.
        """
        new_members = []
        significant = []
        slice_object = self.slice_object
        pareto_length = len(self)

        for ind in population:
            is_dominated = False
            dominates_one = False
            has_twin = False
            to_remove = []
            for i, hofer in enumerate(self):  # hofer = hall of famer
                if not dominates_one and hofer.fitness.dominates(
                    ind.fitness, obj=slice_object
                ):
                    is_dominated = True
                    break
                elif ind.fitness.dominates(hofer.fitness, obj=slice_object):
                    dominates_one = True
                    to_remove.append(i)
                    significant.append(
                        not self.similar_fit(ind.fitness.values, hofer.fitness.values)
                    )
                elif self.similar_fit(
                    ind.fitness.values, hofer.fitness.values
                ) and self.similar(ind.value, hofer.value):
                    has_twin = True
                    break

            for i in reversed(to_remove):  # Remove the dominated hofer
                self.remove(i)
            if not is_dominated and not has_twin:
                # if the pareto front is empty or a new item is added to the pareto front that is progress
                # however if there is only a single objective and it does not significantly dominate then
                # don't count that as significant progress
                if pareto_length == 0:
                    significant.append(True)
                elif numGoals > 1:
                    if len(significant) == 0 or (len(significant) and any(significant)):
                        significant.append(True)

                self.insert(ind)
                new_members.append(ind)

        return new_members, any(significant)

    def hashes(self):
        hashes = {
            hashlib.md5(str(list(individual.value)).encode("utf-8", "ignore")).hexdigest()
            for individual in self.items
        }
        return hashes 

    def getBestScores(self):
        data_meta = numpy.array([i.fitness.values for i in self])
        return numpy.min(data_meta, 0)


class ParetoFrontMeta(ParetoFront):
    def __init__(self, similar=None, similar_fit=None, slice_object=slice(None)):
        super().__init__(similar, similar_fit, slice_object)
        self.best_sse = numpy.inf
        self.best_sse_ind = None
        self.best_rmse = numpy.inf
        self.best_rmse_ind = None

    def hashes(self):
        hashes = super().hashes()
        if self.best_sse_ind:
            hashes.add(hashlib.md5(str(list(self.best_sse_ind.value)).encode("utf-8", "ignore")).hexdigest())
        if self.best_rmse_ind:
            hashes.add(hashlib.md5(str(list(self.best_rmse_ind.value)).encode("utf-8", "ignore")).hexdigest())
        return hashes

    def update(self, population, numGoals):
        """Update the Pareto front hall of fame with the *population* by adding
        the individuals from the population that are not dominated by the hall
        of fame. If any individual in the hall of fame is dominated it is
        removed.

        :param population: A list of individual with a fitness attribute to
                           update the hall of fame with.
        """
        new_members = []
        significant = []
        slice_object = self.slice_object
        pareto_length = len(self)

        for ind in population:
            is_dominated = False
            dominates_one = False
            has_twin = False
            to_remove = []

            ind_sse = ind.fitness.values[-2]
            ind_rmse = ind.fitness.values[-1]

            if ind_sse < self.best_sse:
                self.best_sse = ind_sse
                self.best_sse_ind = copy.deepcopy(ind)

            if ind_rmse < self.best_rmse:
                self.best_rmse = ind_rmse
                self.best_rmse_ind = copy.deepcopy(ind)

            for i, hofer in enumerate(self):  # hofer = hall of famer
                if not dominates_one and hofer.fitness.dominates(
                    ind.fitness, obj=slice_object
                ):
                    is_dominated = True
                    break
                elif ind.fitness.dominates(hofer.fitness, obj=slice_object):
                    dominates_one = True
                    to_remove.append(i)
                    significant.append(
                        not self.similar_fit(ind.fitness.values, hofer.fitness.values)
                    )
                elif self.similar_fit(
                    ind.fitness.values, hofer.fitness.values
                ) and self.similar(ind.value, hofer.value):
                    has_twin = True
                    break

            for i in reversed(to_remove):  # Remove the dominated hofer
                self.remove(i)
            if not is_dominated and not has_twin:
                # if the pareto front is empty or a new item is added to the pareto front that is progress
                # however if there is only a single objective and it does not significantly dominate then
                # don't count that as significant progress
                if pareto_length == 0:
                    significant.append(True)
                elif numGoals > 1:
                    if len(significant) == 0 or (len(significant) and any(significant)):
                        significant.append(True)

                self.insert(ind)
                new_members.append(ind)

                    
        return new_members, any(significant)
    
    def getBestScores(self):
        data_meta = [i.fitness.values for i in self]
        if self.best_sse_ind:
            data_meta.append(self.best_sse_ind.fitness.values)
        if self.best_rmse_ind:
            data_meta.append(self.best_rmse_ind.fitness.values)
        
        data_meta = numpy.array(data_meta)
        return numpy.min(data_meta, 0)


class DummyFront(ParetoFront):
    "Modification of the pareto front in DEAP that takes cache as an argument to update to use for similar comparison"

    def __init__(self, similar=None):
        "This is here for API compatibility, don't do anything"
        if similar is None:
            similar = eq
        super().__init__(similar)

    def update(self, population):
        "do not put anything in this front, it is just needed to maintain compatibility"
        return [], False


def similar(a, b):
    "we only need a parameter to 4 digits of accuracy so have the pareto front only keep up to 5 digits for members of the front"
    a = numpy.frombuffer(a)
    b = numpy.frombuffer(b)
    return numpy.allclose(a,b, rtol=1e-1)


def similar_fit_meta_split(a, b):
    a = numpy.frombuffer(a)
    b = numpy.frombuffer(b)
    return numpy.allclose(a[:3],b[:3], rtol=1e-1)


def similar_fit_meta_sse(a, b):
    "SSE is negative and in the last slot and the only score needed"
    a = numpy.frombuffer(a)
    b = numpy.frombuffer(b)
    return numpy.allclose(a[-2],b[-2], rtol=1e-1)


def similar_fit_meta(cache):
    if cache.allScoreSSE and not cache.MultiObjectiveSSE:
        return similar_fit_meta_sse
    else:
        return similar_fit_meta_split


def similar_fit(cache):
    return similar


def updateParetoFront(halloffame, offspring, cache):
    new_members, significant = halloffame.update(
        [
            offspring,
        ],
        cache.numGoals,
    )
    return bool(new_members), significant


In [328]:
size = 1000
input_dim = 4
output_dim = 8
inputs = numpy.random.random([size,input_dim])
values = numpy.random.random([size,output_dim])

population = []
for input,value in zip(inputs,values):
    population.append(Individual(input,value))

In [354]:
import cadet

data = cadet.H5()
data.filename = r"M:\home\kosh\ibt71\MCMC\Synthetic\Linear\bessel\Lin_MCMC_narrow_2\result.h5"
data.load()

population_real = []
population_meta = []
for input,value,meta in zip(data.root.input,data.root.output, data.root.output_meta):
    population_real.append(Individual(input,value))
    population_meta.append(Individual(input,meta))

In [453]:
cache = Dict()
cache.allScoreSSE = 0
cache.MultiObjectiveSSE = 0
cache.numGoals = output_dim

meta_hof = ParetoFrontMeta(
                similar=similar,
                similar_fit=similar_fit_meta(cache),
                slice_object=slice(-2),
            )

In [454]:
import time

start = time.time()

for idx, pop in enumerate(population_meta):
    new, sig = updateParetoFront(meta_hof, pop, cache)
    print(f"idx {idx} Size {len(meta_hof)} New: {new} Significant {sig}")
    
print(f"Complete in {time.time() - start}")

idx 0 Size 1 New: True Significant True
idx 1 Size 2 New: True Significant True
idx 2 Size 1 New: True Significant True
idx 3 Size 1 New: False Significant False
idx 4 Size 1 New: True Significant True
idx 5 Size 1 New: True Significant True
idx 6 Size 1 New: True Significant True
idx 7 Size 1 New: False Significant False
idx 8 Size 1 New: False Significant False
idx 9 Size 1 New: False Significant False
idx 10 Size 1 New: False Significant False
idx 11 Size 1 New: True Significant True
idx 12 Size 1 New: False Significant False
idx 13 Size 1 New: False Significant False
idx 14 Size 1 New: False Significant False
idx 15 Size 1 New: False Significant False
idx 16 Size 1 New: False Significant False
idx 17 Size 1 New: False Significant False
idx 18 Size 1 New: False Significant False
idx 19 Size 1 New: False Significant False
idx 20 Size 1 New: False Significant False
idx 21 Size 1 New: False Significant False
idx 22 Size 1 New: False Significant False
idx 23 Size 1 New: False Significan

In [455]:
print(meta_hof.getBestScores())
print(numpy.min(data.root.output_meta, 0))

[0.00117982 0.00283424 0.00117855 0.11452122 0.00873479]
[0.00117982 0.00280752 0.00117855 0.11452122 0.00873479]


In [266]:
index = 9
len_self = 10

print(len_self - (index % len_self + 1))

0


In [372]:
import CADETMatch.pareto as pareto

pareto.ParetoFront.getBestScores = ParetoFront.getBestScores

In [449]:
meta_hof_orig = pareto.ParetoFrontMeta(
                similar=pareto.similar,
                similar_fit=pareto.similar_fit_meta(cache),
                slice_object=slice(-2),
            )

In [450]:
import time

start = time.time()

for idx, pop in enumerate(population_meta):
    new, sig = pareto.updateParetoFront(meta_hof_orig, pop, cache)
    print(f"idx {idx} Size {len(meta_hof_orig)} New: {new} Significant {sig}")
    
print(f"Complete in {time.time() - start}")

idx 0 Size 1 New: True Significant True
idx 1 Size 2 New: True Significant True
idx 2 Size 1 New: True Significant True
idx 3 Size 1 New: False Significant False
idx 4 Size 2 New: True Significant True
idx 5 Size 1 New: True Significant True
idx 6 Size 1 New: True Significant True
idx 7 Size 1 New: False Significant False
idx 8 Size 1 New: False Significant False
idx 9 Size 1 New: False Significant False
idx 10 Size 1 New: False Significant False
idx 11 Size 1 New: True Significant True
idx 12 Size 1 New: False Significant False
idx 13 Size 1 New: False Significant False
idx 14 Size 1 New: False Significant False
idx 15 Size 1 New: False Significant False
idx 16 Size 1 New: False Significant False
idx 17 Size 1 New: False Significant False
idx 18 Size 1 New: False Significant False
idx 19 Size 1 New: False Significant False
idx 20 Size 1 New: False Significant False
idx 21 Size 1 New: False Significant False
idx 22 Size 1 New: False Significant False
idx 23 Size 1 New: False Significan

In [451]:
print(meta_hof_orig.getBestScores())
print(numpy.min(data.root.output_meta, 0))

[0.00141026 0.00285181 0.00140961 0.11452122 0.00873479]
[0.00117982 0.00280752 0.00117855 0.11452122 0.00873479]


In [336]:
import sys
del sys.modules['CADETMatch.pareto']

In [342]:
meta_hof_orig.hashes()

AttributeError: 'ParetoFrontMeta' object has no attribute 'hashes'

In [394]:
for i in meta_hof:
    print(i)

Individual(value=array('d', [0.2901262928137375, 0.37046186699535144]), fitness=Fitness(_values=array('d', [0.0011798241901916917, 0.003933653885742849, 0.0011785507178339039, 0.17018942432026, 0.010648193596205186])), best=False)
Individual(value=array('d', [0.2901623189743764, 0.36974030746272524]), fitness=Fitness(_values=array('d', [0.0012524506685658299, 0.003859918139459295, 0.001251284727993851, 0.1727950286950378, 0.010729396030093126])), best=False)
Individual(value=array('d', [0.28999667544644026, 0.3674435400556752]), fitness=Fitness(_values=array('d', [0.0012637711095992987, 0.0028971020970233186, 0.0012629441411706743, 0.17880725550688126, 0.010914459219671959])), best=False)
Individual(value=array('d', [0.28994035781754296, 0.3674435400556752]), fitness=Fitness(_values=array('d', [0.0013078574288113431, 0.0028929049188610723, 0.0013071085715520292, 0.17826802447787918, 0.010897989365189507])), best=False)
Individual(value=array('d', [0.2899081971268209, 0.3680712283194466

In [395]:
for i in meta_hof_orig:
    print(i)

Individual(value=array('d', [0.2860741957502538, 0.39830997437253257]), fitness=Fitness(_values=array('d', [0.00555069743978831, 0.02558735668393275, 0.005509169380249035, 0.11452122087995195, 0.008734793424909987])), best=True)
Individual(value=array('d', [0.289812256321346, 0.36884723483457893]), fitness=Fitness(_values=array('d', [0.0014102633077905935, 0.002851809436994923, 0.0014096101921259319, 0.1723673832271216, 0.010716110867753955])), best=False)


In [401]:
print(meta_hof)

[Individual(value=array('d', [0.2901262928137375, 0.37046186699535144]), fitness=Fitness(_values=array('d', [0.0011798241901916917, 0.003933653885742849, 0.0011785507178339039, 0.17018942432026, 0.010648193596205186])), best=False), Individual(value=array('d', [0.2901623189743764, 0.36974030746272524]), fitness=Fitness(_values=array('d', [0.0012524506685658299, 0.003859918139459295, 0.001251284727993851, 0.1727950286950378, 0.010729396030093126])), best=False), Individual(value=array('d', [0.28999667544644026, 0.3674435400556752]), fitness=Fitness(_values=array('d', [0.0012637711095992987, 0.0028971020970233186, 0.0012629441411706743, 0.17880725550688126, 0.010914459219671959])), best=False), Individual(value=array('d', [0.28994035781754296, 0.3674435400556752]), fitness=Fitness(_values=array('d', [0.0013078574288113431, 0.0028929049188610723, 0.0013071085715520292, 0.17826802447787918, 0.010897989365189507])), best=False), Individual(value=array('d', [0.2899081971268209, 0.36807122831

In [402]:
print(meta_hof_orig)

[Individual(value=array('d', [0.2860741957502538, 0.39830997437253257]), fitness=Fitness(_values=array('d', [0.00555069743978831, 0.02558735668393275, 0.005509169380249035, 0.11452122087995195, 0.008734793424909987])), best=True), Individual(value=array('d', [0.289812256321346, 0.36884723483457893]), fitness=Fitness(_values=array('d', [0.0014102633077905935, 0.002851809436994923, 0.0014096101921259319, 0.1723673832271216, 0.010716110867753955])), best=False)]


In [456]:
cache = Dict()
cache.allScoreSSE = 0
cache.MultiObjectiveSSE = 0
cache.numGoals = output_dim

meta_hof = ParetoFront(
                similar=similar,
                similar_fit=similar_fit(cache),
                slice_object=slice(None),
            )

In [457]:
import time

start = time.time()

for idx, pop in enumerate(population_real):
    new, sig = updateParetoFront(meta_hof, pop, cache)
    print(f"idx {idx} Size {len(meta_hof)} New: {new} Significant {sig}")
    
print(f"Complete in {time.time() - start}")

idx 0 Size 1 New: True Significant True
idx 1 Size 2 New: True Significant True
idx 2 Size 3 New: True Significant True
idx 3 Size 4 New: True Significant True
idx 4 Size 4 New: True Significant True
idx 5 Size 1 New: True Significant True
idx 6 Size 2 New: True Significant True
idx 7 Size 2 New: False Significant False
idx 8 Size 2 New: False Significant False
idx 9 Size 2 New: False Significant False
idx 10 Size 2 New: False Significant False
idx 11 Size 1 New: True Significant True
idx 12 Size 1 New: False Significant False
idx 13 Size 1 New: False Significant False
idx 14 Size 1 New: False Significant False
idx 15 Size 1 New: False Significant False
idx 16 Size 1 New: False Significant False
idx 17 Size 1 New: False Significant False
idx 18 Size 1 New: False Significant False
idx 19 Size 1 New: False Significant False
idx 20 Size 1 New: False Significant False
idx 21 Size 1 New: False Significant False
idx 22 Size 1 New: False Significant False
idx 23 Size 1 New: False Significant 

In [458]:
print(meta_hof.getBestScores())
print(numpy.min(data.root.output, 0))

[2.41470203e-06 2.27898309e-05 1.29440259e-09 1.14511297e-05
 3.71589649e-07 4.79216271e-07]
[2.41470203e-06 2.27898309e-05 1.29440259e-09 1.14511297e-05
 3.71589649e-07 4.79216271e-07]


In [427]:
meta_hof_orig = pareto.ParetoFront(
                similar=pareto.similar,
                similar_fit=pareto.similar_fit(cache),
                slice_object=slice(None),
            )

In [428]:
import time

start = time.time()

for idx, pop in enumerate(population_real):
    new, sig = pareto.updateParetoFront(meta_hof_orig, pop, cache)
    print(f"idx {idx} Size {len(meta_hof_orig)} New: {new} Significant {sig}")
    
print(f"Complete in {time.time() - start}")

idx 0 Size 1 New: True Significant True
idx 1 Size 2 New: True Significant True
idx 2 Size 3 New: True Significant True
idx 3 Size 4 New: True Significant True
idx 4 Size 4 New: True Significant True
idx 5 Size 1 New: True Significant True
idx 6 Size 2 New: True Significant True
idx 7 Size 2 New: False Significant False
idx 8 Size 2 New: False Significant False
idx 9 Size 2 New: False Significant False
idx 10 Size 2 New: False Significant False
idx 11 Size 1 New: True Significant True
idx 12 Size 1 New: False Significant False
idx 13 Size 1 New: False Significant False
idx 14 Size 1 New: False Significant False
idx 15 Size 1 New: False Significant False
idx 16 Size 1 New: False Significant False
idx 17 Size 1 New: False Significant False
idx 18 Size 1 New: False Significant False
idx 19 Size 1 New: False Significant False
idx 20 Size 1 New: False Significant False
idx 21 Size 1 New: False Significant False
idx 22 Size 1 New: False Significant False
idx 23 Size 1 New: False Significant 

In [429]:
print(meta_hof_orig.getBestScores())
print(numpy.min(data.root.output, 0))

[2.60366731e-06 2.27898309e-05 1.29440259e-09 1.14511297e-05
 3.71589649e-07 4.79216271e-07]
[2.41470203e-06 2.27898309e-05 1.29440259e-09 1.14511297e-05
 3.71589649e-07 4.79216271e-07]
